<h1> SVG vs WebGL </h1>

In [25]:
import plotly.express as px

import pandas as pd
import numpy as np
np.random.seed(1)

N = 100000

df = pd.DataFrame(dict(x=np.random.randn(N),
                       y=np.random.randn(N)))

fig = px.scatter(df, x="x", y="y", render_mode='webgl')

fig.update_traces(marker_line=dict(width=1, color='DarkSlateGray'))

fig.show()
#export plot as html
fig.write_html("plots/plotly_webgl.html")



In [26]:
import plotly.express as px

import pandas as pd
import numpy as np
np.random.seed(1)

N = 100000

df = pd.DataFrame(dict(x=np.random.randn(N),
                       y=np.random.randn(N)))

fig = px.scatter(df, x="x", y="y", render_mode='svg')

fig.update_traces(marker_line=dict(width=1, color='DarkSlateGray'))

#export plot as html
fig.write_html("plots/plotly_svg.html")

<h1> Datasahder vs Plotly Express </h1>

In [27]:
import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/uber-rides-data1.csv')
dff = df.query('Lat < 40.79').query('Lat > 40.76').query('Lon > -74.02').query('Lon < -73.91')

import datashader as ds
cvs = ds.Canvas(plot_width=1000, plot_height=1000)
agg = cvs.points(dff, x='Lon', y='Lat')
# agg is an xarray object, see http://xarray.pydata.org/en/stable/ for more details
coords_lat, coords_lon = agg.coords['Lat'].values, agg.coords['Lon'].values
# Corners of the image, which need to be passed to mapbox
coordinates = [[coords_lon[0], coords_lat[0]],
               [coords_lon[-1], coords_lat[0]],
               [coords_lon[-1], coords_lat[-1]],
               [coords_lon[0], coords_lat[-1]]]

from colorcet import fire
import datashader.transfer_functions as tf
img = tf.shade(agg, cmap=fire)[::-1].to_pil()

import plotly.express as px
# Trick to create rapidly a figure with mapbox axes
fig = px.scatter_mapbox(dff[:1], lat='Lat', lon='Lon', zoom=12)
# Add the datashader image as a mapbox layer image
fig.update_layout(mapbox_style="carto-darkmatter",
                 mapbox_layers = [
                {
                    "sourcetype": "image",
                    "source": img,
                    "coordinates": coordinates
                }]
)
#export plot as html
fig.write_html("plots/datashader_ampbox.html")

In [28]:
import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/uber-rides-data1.csv')
dff = df.query('Lat < 40.79').query('Lat > 40.76').query('Lon > -74.02').query('Lon < -73.91')

#no datashader
import plotly.express as px
#represent as heatmap fire color
fig = px.scatter_mapbox(dff, lat='Lat', lon='Lon', zoom=12, color_continuous_scale=px.colors.cyclical.IceFire, opacity=0.01)


fig.update_layout(mapbox_style="carto-darkmatter")
#export plot as html
fig.write_html("plots/plotly_mapbox.html")


# Design Principles of Interactive Visualization: Shneidermans Mantra

In [75]:
#read data
import pandas as pd
df = pd.read_csv('data/ml-latest/movies.csv')

In [76]:
df.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [77]:
#extract year from title
df['year'] = df.title.str.extract('.*\((\d{4})\).*', expand=False)
#drop movies without year
df = df.dropna(subset=['year'])
#convert year to int
df['year'] = df['year'].astype(int)

#remove year from title
df['title'] = df.title.str.replace('(\(\d\d\d\d\))', '')

#extract genres
df['genres'] = df.genres.str.split('|')
#doesnt work
df = df.dropna(subset=['genres'])
#represent each movie for each genre
df = df.explode('genres')

df.head()

/var/folders/v2/51sbk7ln57325w479zxv0dqc0000gn/T/ipykernel_77336/2995181027.py:9: FutureWarning:

The default value of regex will change from True to False in a future version.



movieId       title     genres  year
0        1  Toy Story   Adventure  1995
0        1  Toy Story   Animation  1995
0        1  Toy Story    Children  1995
0        1  Toy Story      Comedy  1995
0        1  Toy Story     Fantasy  1995

In [78]:
#count movies per genre and plot with plotly
import plotly.express as px
fig = px.histogram(df, x="genres", color="genres", title="Movies per genre")
# if you click on one bar, the other bars will be greyed out
fig.update_traces(marker_line_color='rgb(8,48,107)',
                    marker_line_width=1.5, opacity=0.6)


fig.show()

In [87]:
# now make one plot for genre Sci-Fi on x axis year on y axis count
df_scifi = df.query('genres == "Sci-Fi"')
#set color to emerald green
fig = px.histogram(df_scifi, x="year", color="genres", title="Sci-Fi movies per year", color_discrete_sequence=
    ["#2ecc71"])
# if you click on one bar, the other bars will be greyed out
#add a date range slider
fig.update_layout(
    xaxis=dict(
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)

fig.update_traces(marker_line_color='rgb(8,48,107)',
                    marker_line_width=1.5, opacity=0.6)

fig.show()



Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on


/Users/nicolarohner/Documents/GitHub/ivi/.venv/lib/python3.9/site-packages/traitlets/traitlets.py:2548: FutureWarning: Supporting extra quotes around strings is deprecated in traitlets 5.0. You can use 'hmac-sha256' instead of '"hmac-sha256"' if you require traitlets >=5.
  warn(
/Users/nicolarohner/Documents/GitHub/ivi/.venv/lib/python3.9/site-packages/traitlets/traitlets.py:2499: FutureWarning: Supporting extra quotes around Bytes is deprecated in traitlets 5.0. Use 'ab180674-dcea-4178-884b-5e4e6a9cca00' instead of 'b"ab180674-dcea-4178-884b-5e4e6a9cca00"'.
  warn(
Traceback (most recent call last):
  File "/Users/nicolarohner/Documents/GitHub/ivi/.venv/lib/python3.9/site-packages/ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "/Users/nicolarohner/Documents/GitHub/ivi/.venv/lib/python3.9/site-packages/traitlets/config/application.py", line 1042, in launch_instance
    app.initialize(argv)
  File "/Users/nicolarohner/Documents/GitHub/ivi/.venv/lib/py

SystemExit: 1